In [2]:
%cd ..
%load_ext autoreload
%autoreload 2

from pykitti.tracking import KittiTrackingLabels
from PyKitti2Dataset import PyKitti2
from hugeica import *
from Mine import *
from hugeica import Adam_Lie
from Crop import crop

import imageio
from PIL import Image

import numpy as np
import matplotlib.pyplot as plt
import torch.nn as nn
import torch
import meshplot as mp

from sklearn.neighbors import NearestNeighbors
from AutoCalibration import *


def log_results(log):

    metrics = [] 
    i  = 1
    sortby, ascending = "loss", False
    
    for r, interval_t, interval_r in log:

        Q_cos = r[i].sort_values(sortby, ascending=ascending)["Q_cos"].values[-1]
        t_l2 = r[i].sort_values(sortby, ascending=ascending)["t_l2"].values[-1]

        metrics.append([Q_cos, t_l2])

        print(interval_r, interval_t)

    print("loss", np.asarray(metrics).mean(0), np.asarray(metrics).std(0))

    metrics = []
    i  = 1
    sortby, ascending = "loss", False
    sortby, ascending = "mi", True
    
    for r, interval_t, interval_r in log:

        Q_cos = r[i].sort_values(sortby, ascending=ascending)["Q_cos"].values[-1]
        t_l2 = r[i].sort_values(sortby, ascending=ascending)["t_l2"].values[-1]

        metrics.append([Q_cos, t_l2])

    print("mi", np.asarray(metrics).mean(0), np.asarray(metrics).std(0))

    metrics = [] 
    i  = 1
    sortby, ascending = "loss", False
    sortby, ascending = "mi", True
    
    for r, interval_t, interval_r in log:

        Q_cos = r[i]["Q_cos"].values[-1]
        t_l2 = r[i]["t_l2"].values[-1]

        metrics.append([Q_cos, t_l2])

    print("Converged", np.asarray(metrics).mean(0), np.asarray(metrics).std(0))


basedir = "/home/ios/data3/kitti/tracking/training"
seq = "0000"

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


# Load Data

In [3]:
kitti = PyKitti2(basedir, seq, with_labels="box")   

image = kitti[0][1]
box = kitti[0][4][0].astype(int)
label = kitti[0][5][0]
label_num = KittiTrackingLabels.classes.index(label)
image = np.asarray(image).copy()

def box_to_image(image, box, border=2):
    x1,y1, x2, y2 = box
    inside = image[y1:y1+y2, x1:x1+x2, :].copy()
    image[y1:y1+y2, x1:x1+x2, :] = (255, 255, 255)
    image[y1+border:y1+y2-border, x1+border:x1+x2-border, :] = inside[border:-border, border:-border, :]
    plt.rcParams["figure.figsize"] = (200, 100)
    plt.imshow(image)
    plt.show()

def px_in_box(query_px, box):
    x1,y1, x2, y2 = box

    a = np.logical_and(query_px[:, 0] >= x1, 
                        query_px[:, 0] <= (x1 + x2)) 
    b = np.logical_and(query_px[:, 1] >= y1, 
                          query_px[:, 1] <= (y1 + y2))
    return np.logical_and(a, b)    
    
#box_to_image(image, box)

files 154


/home/ios/anaconda3/envs/pytorch/lib/python3.7/site-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)


In [4]:
datas = [PyKitti2(basedir, f"{i:04d}", with_labels="none") for i in range(10)]

kitti1 = datas[0]
initRT = kitti1.calib.T_cam2_velo.copy()

files 154
files 447
files 233
files 144
files 314


/home/ios/anaconda3/envs/pytorch/lib/python3.7/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


files 297
files 270
files 800
files 390
files 803


In [5]:
# Kitti dataset is recalibrated on different days, so we can just test on sequences that have the same calibration
datas_test1 = [PyKitti2(basedir, f"{i:04d}", with_labels="none") for i in range(10,14)]

files 294
files 373
files 78
files 340


In [6]:
datas_test2 = [PyKitti2(basedir, f"{i:04d}", with_labels="none") for i in range(14,18)]

files 106
files 376
files 209
files 145


In [7]:
datas_test3 = [PyKitti2(basedir, f"{i:04d}", with_labels="none") for i in range(18,20)]

files 339
files 1059


In [8]:
datas_test4 = [PyKitti2(basedir, f"{i:04d}", with_labels="none") for i in range(20,21)]

files 837


In [9]:
datas_test = [datas_test1, datas_test2, datas_test3, datas_test4]

In [10]:
calib0 = datas_test1[0].calib.T_cam2_velo
calib1 = datas_test2[0].calib.T_cam2_velo
calib2 = datas_test3[0].calib.T_cam2_velo
calib3 = datas_test4[0].calib.T_cam2_velo

calib = [calib0, calib1, calib2, calib3]

datas_test

[[PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0010)[294],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0011)[373],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0012)[78],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0013)[340]],
 [PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0014)[106],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0015)[376],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0016)[209],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0017)[145]],
 [PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0018)[314],
  PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0019)[1059]],
 [PyKitti2(base_path=/home/ios/data3/kitti/tracking/training, sequence=0020)[837]]]

# Testing accuracy

## Accuracy no grad

In [217]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_r = np.random.uniform(-0.000001, 0.0000001, (3,))
        interval_t = np.random.uniform(-0.6, 0.6, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=False,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.07761313 -0.09555864 -0.20359821] r:  [-5.20405608e-07 -9.71481145e-07 -3.95371274e-07] 

MINE weight pool size is 1000
#   0: nll: 0.74/0.58, mi: -0.047/ 0.615, acc: 40.0/70.7, eps: 0.22220, R=[-0.0, -0.0, -0.0], t=0.22, Q_cos=0.00
#  30: nll: 0.90/0.52, mi: -0.680/ 1.229, acc: 60.0/74.7, eps: 0.17479, R=[-0.0, -0.0, -0.0], t=0.05, Q_cos=0.00
Saved checkpoint
#  60: nll: 0.41/0.52, mi:  1.446/ 0.967, acc: 80.0/72.8, eps: 0.01334, R=[-0.0, -0.0, -0.0], t=0.03, Q_cos=0.00
#  90: nll: 0.61/0.58, mi:  0.448/ 0.862, acc: 60.0/71.0, eps: 0.02646, R=[-0.0, -0.0, -0.0], t=0.06, Q_cos=0.00
# 120: nll: 0.49/0.51, mi:  1.194/ 1.015, acc: 85.0/73.1, eps: 0.04081, R=[-0.0, -0.0, -0.0], t=0.02, Q_cos=0.00
# 150: nll: 0.64/0.56, mi:  0.527/ 0.778, acc: 62.5/72.5, eps: 0.04962, R=[-0.0, -0.0, -0.0], t=0.07, Q_cos=0.00
# 180: nll: 0.72/0.52, mi:  0.245/ 0.854, acc: 55.0/73.6, eps: 0.04038, R=[-0.0, -0.0, -0.0], t=0.03, Q_cos=0.00
# 210: nll: 0.59/0.54, mi:  0.49

KeyboardInterrupt: 

In [219]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 

    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]


    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)


    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.3, 0.3, (3,))
        interval_r = np.random.uniform(-2, 2, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            #ac.load_state_dict(torch.load("checkpoints/checkpoint_best_mi.pth.tar"))
            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))

log_results(log)

Using test set # 3

 Distortion t:  [-0.03840306 -0.28444426  0.02979749] r:  [-0.25871043 -0.31852879 -0.67866072] 

MINE weight pool size is 1000
#   0: nll: 0.73/0.68, mi:  0.222/ 0.209, acc: 60.0/65.8, eps: 0.29898, R=[-0.2, -0.26, -0.62], t=0.30, Q_cos=0.70
#  30: nll: 0.62/0.56, mi:  0.195/ 0.725, acc: 70.0/70.0, eps: 0.11567, R=[-0.82, 0.07, -0.94], t=0.18, Q_cos=1.25
Saved checkpoint
#  60: nll: 0.60/0.51, mi:  0.736/ 0.966, acc: 80.0/74.5, eps: 0.03123, R=[-0.61, 0.07, -0.52], t=0.21, Q_cos=0.81
Saved checkpoint
#  90: nll: 0.66/0.56, mi:  0.064/ 0.915, acc: 57.5/72.1, eps: 0.03683, R=[-0.91, 0.01, -0.51], t=0.18, Q_cos=1.04
# 120: nll: 0.39/0.50, mi:  1.427/ 1.137, acc: 80.0/74.2, eps: 0.01358, R=[-0.81, 0.0, -0.06], t=0.19, Q_cos=0.81
Saved checkpoint
# 150: nll: 0.64/0.55, mi:  0.463/ 0.887, acc: 72.5/73.8, eps: 0.01983, R=[-0.94, 0.01, 0.44], t=0.17, Q_cos=1.04
# 180: nll: 0.59/0.54, mi:  0.698/ 0.817, acc: 77.5/71.8, eps: 0.00799, R=[-0.74, 0.08, 0.19], t=0.18, Q_cos=0.77

In [216]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.6, 0.6, (3,))
        interval_r = np.random.uniform(-2, 2, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            #ac.load_state_dict(torch.load("checkpoints/checkpoint_best_mi.pth.tar"))
            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.07680612 -0.56888852  0.05959497] r:  [-0.25871043 -0.31852879 -0.67866072] 

MINE weight pool size is 1000
#   0: nll: 0.75/0.81, mi:  0.041/-0.258, acc: 60.0/57.4, eps: 0.56745, R=[-0.32, -0.26, -0.62], t=0.57, Q_cos=0.75
#  30: nll: 0.93/0.69, mi: -0.552/ 0.060, acc: 40.0/64.0, eps: 0.08524, R=[-0.8, -0.07, -1.08], t=0.48, Q_cos=1.34
#  60: nll: 0.83/0.63, mi: -0.420/ 0.458, acc: 50.0/68.9, eps: 0.10887, R=[-1.62, -0.19, -1.41], t=0.37, Q_cos=2.16
Saved checkpoint
#  90: nll: 0.63/0.65, mi:  0.555/ 0.385, acc: 70.0/64.9, eps: 0.00257, R=[-1.51, 0.03, -1.11], t=0.37, Q_cos=1.87
# 120: nll: 0.49/0.57, mi:  1.047/ 0.732, acc: 75.0/70.7, eps: 0.04205, R=[-1.48, -0.06, -1.06], t=0.33, Q_cos=1.82
Saved checkpoint
# 150: nll: 0.86/0.57, mi: -0.315/ 0.519, acc: 52.5/70.7, eps: 0.00454, R=[-1.28, -0.05, -0.89], t=0.33, Q_cos=1.56
# 180: nll: 0.69/0.57, mi: -0.078/ 0.653, acc: 52.5/71.6, eps: 0.02127, R=[-1.22, 0.17, -0.15], t=0.31, Q_cos=1.24
# 210: nl

In [220]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.0000001, 0.0000001, (3,))
        interval_r = np.random.uniform(-5, 5, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            #ac.load_state_dict(torch.load("checkpoints/checkpoint_best_mi.pth.tar"))
            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=False,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-1.28010196e-08 -9.48147536e-08  9.93249558e-09] r:  [-0.64677607 -0.79632198 -1.69665179] 

MINE weight pool size is 1000
#   0: nll: 0.72/0.76, mi:  0.064/ 0.125, acc: 52.5/62.6, eps: 0.05020, R=[-0.71, -0.74, -1.75], t=0.00, Q_cos=2.03
#  30: nll: 0.71/0.61, mi: -0.054/ 0.453, acc: 65.0/69.4, eps: 0.00728, R=[-0.49, 0.03, -1.67], t=0.00, Q_cos=1.74
Saved checkpoint
#  60: nll: 0.59/0.54, mi:  0.609/ 0.824, acc: 77.5/71.1, eps: 0.01360, R=[0.35, -0.03, -1.13], t=0.00, Q_cos=1.19
Saved checkpoint
#  90: nll: 0.74/0.59, mi: -0.151/ 0.745, acc: 62.5/69.6, eps: 0.01561, R=[0.04, -0.03, -0.55], t=0.00, Q_cos=0.56
# 120: nll: 0.66/0.52, mi:  0.307/ 0.997, acc: 65.0/71.4, eps: 0.00659, R=[-0.09, -0.07, -0.27], t=0.00, Q_cos=0.29
Saved checkpoint
# 150: nll: 0.57/0.52, mi:  1.066/ 0.938, acc: 65.0/75.1, eps: 0.00078, R=[-0.13, 0.12, -0.19], t=0.00, Q_cos=0.26
# 180: nll: 0.44/0.52, mi:  1.208/ 1.039, acc: 75.0/75.3, eps: 0.00446, R=[-0.07, -0.0, -0.02], t

In [221]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.3, 0.3, (3,))
        interval_r = np.random.uniform(-5, 5, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            #ac.load_state_dict(torch.load("checkpoints/checkpoint_best_mi.pth.tar"))
            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.03840306 -0.28444426  0.02979749] r:  [-0.64677607 -0.79632198 -1.69665179] 

MINE weight pool size is 1000
#   0: nll: 0.72/0.62, mi:  0.309/ 0.564, acc: 65.0/69.1, eps: 0.28325, R=[-0.71, -0.74, -1.75], t=0.28, Q_cos=2.03
#  30: nll: 0.79/0.57, mi:  0.006/ 0.644, acc: 62.5/71.6, eps: 0.03435, R=[-0.49, -0.28, -1.49], t=0.32, Q_cos=1.60
Saved checkpoint
#  60: nll: 0.54/0.56, mi:  0.750/ 0.723, acc: 72.5/70.7, eps: 0.04664, R=[-0.55, -0.52, -1.4], t=0.27, Q_cos=1.59
Saved checkpoint
#  90: nll: 0.47/0.56, mi:  1.103/ 0.761, acc: 82.5/71.5, eps: 0.08536, R=[-0.8, -0.26, -1.51], t=0.18, Q_cos=1.73
Saved checkpoint
# 120: nll: 0.64/0.50, mi:  0.308/ 1.114, acc: 65.0/73.2, eps: 0.01486, R=[-0.56, -0.27, -0.82], t=0.20, Q_cos=1.03
Saved checkpoint
# 150: nll: 0.74/0.55, mi:  0.281/ 0.777, acc: 72.5/73.9, eps: 0.02467, R=[-0.71, -0.05, -0.6], t=0.17, Q_cos=0.93
# 180: nll: 0.56/0.56, mi:  0.987/ 0.687, acc: 75.0/71.1, eps: 0.01370, R=[-0.42, -0.02, -0

In [218]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.6, 0.6, (3,))
        interval_r = np.random.uniform(-5, 5, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            #ac.load_state_dict(torch.load("checkpoints/checkpoint_best_mi.pth.tar"))
            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.07680612 -0.56888852  0.05959497] r:  [-0.64677607 -0.79632198 -1.69665179] 

MINE weight pool size is 1000
#   0: nll: 0.78/0.89, mi:  0.014/-0.442, acc: 60.0/56.0, eps: 0.58941, R=[-0.59, -0.85, -1.64], t=0.59, Q_cos=1.94
#  30: nll: 0.80/0.71, mi: -0.444/-0.021, acc: 62.5/63.2, eps: 0.02814, R=[-0.54, -0.3, -1.56], t=0.62, Q_cos=1.68
#  60: nll: 0.83/0.56, mi: -0.894/ 0.707, acc: 60.0/71.6, eps: 0.07408, R=[-1.06, -0.01, -1.9], t=0.54, Q_cos=2.18
#  90: nll: 0.84/0.72, mi: -0.255/ 0.144, acc: 57.5/63.7, eps: 0.01943, R=[-1.32, 0.01, -2.07], t=0.52, Q_cos=2.45
# 120: nll: 0.63/0.62, mi:  0.461/ 0.565, acc: 67.5/69.5, eps: 0.02003, R=[-1.46, -0.01, -2.19], t=0.50, Q_cos=2.64
# 150: nll: 0.62/0.67, mi:  0.289/ 0.324, acc: 70.0/64.9, eps: 0.04363, R=[-1.6, 0.05, -2.0], t=0.46, Q_cos=2.56
# 180: nll: 0.72/0.61, mi: -0.110/ 0.407, acc: 57.5/67.6, eps: 0.01342, R=[-1.39, -0.02, -1.47], t=0.47, Q_cos=2.03
# 210: nll: 0.67/0.62, mi:  0.153/ 0.480, acc:

In [222]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.3, 0.3, (3,))
        interval_r = np.random.uniform(-7, 7, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.03840306 -0.28444426  0.02979749] r:  [-0.9054865  -1.11485077 -2.37531251] 

MINE weight pool size is 1000
#   0: nll: 0.93/0.76, mi: -0.653/ 0.041, acc: 35.0/62.3, eps: 0.30579, R=[-0.85, -1.06, -2.32], t=0.30, Q_cos=2.69
#  30: nll: 0.84/0.64, mi: -0.468/ 0.302, acc: 65.0/67.5, eps: 0.03922, R=[-0.93, -0.58, -2.69], t=0.34, Q_cos=2.91
Saved checkpoint
#  60: nll: 0.63/0.68, mi:  0.626/ 0.208, acc: 67.5/64.0, eps: 0.04314, R=[-0.83, -0.18, -2.3], t=0.38, Q_cos=2.45
#  90: nll: 0.72/0.63, mi: -0.009/ 0.421, acc: 52.5/69.6, eps: 0.08094, R=[-1.17, -0.52, -1.66], t=0.30, Q_cos=2.10
Saved checkpoint
# 120: nll: 0.64/0.59, mi:  0.591/ 0.572, acc: 67.5/68.8, eps: 0.01114, R=[-1.07, -0.23, -1.06], t=0.32, Q_cos=1.52
Saved checkpoint
# 150: nll: 0.83/0.60, mi: -0.135/ 0.523, acc: 50.0/68.4, eps: 0.00494, R=[-0.97, -0.26, -0.91], t=0.32, Q_cos=1.36
# 180: nll: 0.57/0.55, mi: -0.043/ 0.726, acc: 77.5/72.2, eps: 0.03505, R=[-1.1, -0.27, -0.78], t=0.29, Q_

In [223]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.6, 0.6, (3,))
        interval_r = np.random.uniform(-7, 7, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.07680612 -0.56888852  0.05959497] r:  [-0.9054865  -1.11485077 -2.37531251] 

MINE weight pool size is 1000
#   0: nll: 0.72/0.78, mi:  0.339/-0.082, acc: 67.5/61.6, eps: 0.57144, R=[-0.97, -1.06, -2.43], t=0.57, Q_cos=2.83
#  30: nll: 0.63/0.66, mi:  0.265/ 0.258, acc: 65.0/65.9, eps: 0.08335, R=[-1.42, -0.23, -2.76], t=0.48, Q_cos=3.12
#  60: nll: 0.65/0.66, mi:  0.231/ 0.391, acc: 60.0/67.5, eps: 0.04229, R=[-1.65, -0.47, -2.89], t=0.44, Q_cos=3.36
Saved checkpoint
#  90: nll: 0.64/0.73, mi:  0.425/-0.024, acc: 70.0/61.9, eps: 0.03305, R=[-1.88, -0.4, -3.08], t=0.40, Q_cos=3.64
# 120: nll: 0.69/0.70, mi:  0.023/ 0.100, acc: 57.5/64.4, eps: 0.01082, R=[-1.82, -0.15, -2.97], t=0.41, Q_cos=3.49
# 150: nll: 0.78/0.75, mi: -0.131/-0.030, acc: 45.0/59.6, eps: 0.01450, R=[-1.74, -0.06, -2.71], t=0.40, Q_cos=3.22
# 180: nll: 0.59/0.71, mi:  0.405/ 0.062, acc: 67.5/64.6, eps: 0.05658, R=[-1.88, -0.14, -2.53], t=0.34, Q_cos=3.16
# 210: nll: 0.74/0.63, m

In [224]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.3, 0.3, (3,))
        interval_r = np.random.uniform(-8, 8, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.03840306 -0.28444426  0.02979749] r:  [-1.03484172 -1.27411517 -2.71464286] 

MINE weight pool size is 1000
#   0: nll: 0.72/0.83, mi:  0.217/-0.317, acc: 60.0/60.3, eps: 0.29083, R=[-1.09, -1.33, -2.77], t=0.28, Q_cos=3.27
#  30: nll: 0.66/0.66, mi:  0.254/ 0.109, acc: 65.0/66.5, eps: 0.01333, R=[-1.18, -0.82, -2.88], t=0.27, Q_cos=3.23
#  60: nll: 0.73/0.69, mi: -0.166/ 0.243, acc: 52.5/66.0, eps: 0.05676, R=[-0.93, -0.21, -2.64], t=0.33, Q_cos=2.81
Saved checkpoint
#  90: nll: 0.92/0.64, mi: -0.403/ 0.403, acc: 45.0/68.6, eps: 0.05279, R=[-1.18, -0.27, -2.68], t=0.27, Q_cos=2.94
Saved checkpoint
# 120: nll: 0.73/0.68, mi: -0.219/ 0.345, acc: 60.0/67.5, eps: 0.01017, R=[-1.18, -0.32, -2.28], t=0.26, Q_cos=2.59
# 150: nll: 0.84/0.61, mi: -0.330/ 0.455, acc: 47.5/69.0, eps: 0.02856, R=[-0.86, -0.22, -1.89], t=0.30, Q_cos=2.09
Saved checkpoint
# 180: nll: 0.70/0.61, mi:  0.188/ 0.472, acc: 67.5/66.0, eps: 0.03182, R=[-0.73, -0.04, -1.31], t=0.33, 

In [225]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.6, 0.6, (3,))
        interval_r = np.random.uniform(-8, 8, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.07680612 -0.56888852  0.05959497] r:  [-1.03484172 -1.27411517 -2.71464286] 

MINE weight pool size is 1000
#   0: nll: 0.89/0.84, mi: -0.598/-0.319, acc: 52.5/59.7, eps: 0.57259, R=[-0.98, -1.21, -2.77], t=0.57, Q_cos=3.19
#  30: nll: 0.89/0.63, mi: -0.572/ 0.363, acc: 50.0/67.3, eps: 0.03302, R=[-0.95, -0.92, -2.59], t=0.53, Q_cos=2.91
#  60: nll: 0.78/0.68, mi: -0.391/ 0.230, acc: 52.5/65.1, eps: 0.00446, R=[-1.03, -0.57, -2.85], t=0.53, Q_cos=3.09
#  90: nll: 0.70/0.77, mi:  0.242/-0.184, acc: 67.5/62.1, eps: 0.02618, R=[-1.4, -0.34, -2.83], t=0.50, Q_cos=3.18
# 120: nll: 0.60/0.66, mi:  0.733/ 0.277, acc: 67.5/61.6, eps: 0.00897, R=[-1.04, -0.32, -2.22], t=0.51, Q_cos=2.47
# 150: nll: 0.85/0.62, mi: -0.153/ 0.373, acc: 62.5/68.4, eps: 0.08189, R=[-1.33, -0.23, -1.73], t=0.43, Q_cos=2.19
Saved checkpoint
# 180: nll: 0.65/0.57, mi:  0.336/ 0.613, acc: 70.0/70.1, eps: 0.03946, R=[-1.37, -0.29, -1.1], t=0.39, Q_cos=1.78
Saved checkpoint
# 210: n

In [226]:
log = []
np.random.seed(2)

t = 2
for i in [3,2,1,0]: 
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32)
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    for _ in range(t):
        interval_t = np.random.uniform(-0.3, 0.3, (3,))
        interval_r = np.random.uniform(-9, 9, (3,))
        print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
        ac.distort_calibration(interval_t, interval_r)

        for iters, lr in [(4000, 1e-3), (2000, 1e-4), (1000, 1e-5)]:

            ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
            ac.best_mi = 0.
            r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                       log_avg_window=1,
                       n_test_batches=20, 
                       valid_ratio=0.1, 
                       grad_SE=True, 
                       grad_R=True,
                       grad_T=True,
                       weight_pool_root="checkpoints/mi_model_p96_small_1000",
                       sample_weight_pool=True)

        log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 3

 Distortion t:  [-0.03840306 -0.28444426  0.02979749] r:  [-1.16419693 -1.43337956 -3.05397322] 

MINE weight pool size is 1000
#   0: nll: 0.79/0.82, mi: -0.343/-0.148, acc: 47.5/60.5, eps: 0.31221, R=[-1.1, -1.49, -3.11], t=0.30, Q_cos=3.63
#  30: nll: 0.69/0.65, mi:  0.381/ 0.305, acc: 60.0/66.5, eps: 0.05425, R=[-0.8, -0.79, -3.45], t=0.36, Q_cos=3.63
#  60: nll: 0.55/0.69, mi:  0.790/ 0.182, acc: 70.0/64.7, eps: 0.03499, R=[-1.11, -0.44, -3.69], t=0.32, Q_cos=3.89
#  90: nll: 0.62/0.70, mi:  0.758/ 0.327, acc: 60.0/65.3, eps: 0.06659, R=[-0.75, -0.32, -3.14], t=0.39, Q_cos=3.25
Saved checkpoint
# 120: nll: 0.79/0.70, mi: -0.547/ 0.210, acc: 47.5/65.1, eps: 0.01233, R=[-0.59, -0.28, -3.0], t=0.40, Q_cos=3.07
# 150: nll: 0.64/0.69, mi:  0.027/ 0.252, acc: 50.0/65.6, eps: 0.00801, R=[-0.59, -0.2, -2.66], t=0.40, Q_cos=2.74
# 180: nll: 0.59/0.63, mi:  0.761/ 0.346, acc: 62.5/66.5, eps: 0.05824, R=[-0.67, -0.3, -2.23], t=0.34, Q_cos=2.35
Saved checkpoint
# 210: nll:

RecursionError: maximum recursion depth exceeded in comparison

In [ ]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.2, (3,))
    interval_r = np.random.uniform(0, 2, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 1

 Distortion t:  [0.01846772 0.03725204 0.06911215] r:  [0.79353495 1.07763347 0.83838903] 

#   0: nll: 0.99/0.82, mi: -0.919/-0.135, acc: 45.0/56.0, eps: 0.10004, R=[0.74, 1.02, 0.89], t=0.09, Q_cos=1.54
#  30: nll: 0.38/0.46, mi:  1.818/ 1.098, acc: 85.0/77.5, eps: 0.05084, R=[0.35, 0.64, 0.82], t=0.15, Q_cos=1.10
#  60: nll: 0.35/0.49, mi:  1.722/ 0.975, acc: 85.0/76.0, eps: 0.03569, R=[0.26, 0.46, 0.06], t=0.11, Q_cos=0.53
#  90: nll: 0.45/0.45, mi:  1.112/ 1.142, acc: 80.0/79.5, eps: 0.06716, R=[0.25, 0.42, -0.22], t=0.05, Q_cos=0.54
Saved checkpoint
# 120: nll: 0.50/0.48, mi:  0.925/ 1.041, acc: 80.0/77.2, eps: 0.01032, R=[-0.0, 0.37, -0.24], t=0.04, Q_cos=0.44
# 150: nll: 0.51/0.59, mi:  1.190/ 0.580, acc: 75.0/68.0, eps: 0.00077, R=[0.29, 0.3, -0.23], t=0.04, Q_cos=0.48
# 180: nll: 0.61/0.50, mi:  0.308/ 1.093, acc: 67.5/76.2, eps: 0.00665, R=[-0.12, 0.29, -0.09], t=0.03, Q_cos=0.33
# 210: nll: 0.24/0.49, mi:  2.898/ 1.187, acc: 90.0/74.8, eps: 0.00004, R=[0

In [128]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.6, (3,))
    interval_r = np.random.uniform(0, 2, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 1

 Distortion t:  [0.05540316 0.11175613 0.20733644] r:  [0.79353495 1.07763347 0.83838903] 

#   0: nll: 0.73/0.76, mi: -0.067/ 0.144, acc: 50.0/60.0, eps: 0.26042, R=[0.74, 1.14, 0.78], t=0.26, Q_cos=1.56
#  30: nll: 1.05/0.62, mi: -0.913/ 0.511, acc: 52.5/69.8, eps: 0.04716, R=[0.63, 0.66, 0.39], t=0.31, Q_cos=0.99
Saved checkpoint
#  60: nll: 0.46/0.49, mi:  1.077/ 0.940, acc: 77.5/75.8, eps: 0.05828, R=[0.58, 0.37, 0.21], t=0.25, Q_cos=0.72
Saved checkpoint
#  90: nll: 0.40/0.54, mi:  1.657/ 0.817, acc: 80.0/73.0, eps: 0.07501, R=[0.55, 0.34, 0.17], t=0.17, Q_cos=0.67
# 120: nll: 0.39/0.48, mi:  1.382/ 1.081, acc: 82.5/76.0, eps: 0.02037, R=[0.59, 0.27, 0.16], t=0.15, Q_cos=0.66
Saved checkpoint
# 150: nll: 0.40/0.47, mi:  1.326/ 1.199, acc: 80.0/77.5, eps: 0.00834, R=[0.46, 0.27, 0.0], t=0.14, Q_cos=0.54
Saved checkpoint
# 180: nll: 0.53/0.41, mi:  0.515/ 1.527, acc: 77.5/81.2, eps: 0.01462, R=[0.19, 0.18, -0.11], t=0.13, Q_cos=0.29
Saved checkpoint
# 210: nll: 

In [108]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)

#[1.98383737 2.69408367 2.09597257] [0.01846772 0.03725204 0.06911215]
#[3.26027964 1.74430323 2.3616742 ] [0.19460976 0.03302958 0.1130815 ]
#[4.06443208 1.67878799 1.52221705] [0.15672174 0.09449057 0.12106924]
#[1.7550374  3.43247292 1.73054533] [0.08690141 0.02554955 0.16466661]
#[1.93367646 1.1723489  4.48125799] [0.16164821 0.13586225 0.16449743]
#loss [0.17835711 0.02630982] [0.04516975 0.01452324]
#mi [0.17299906 0.02572074] [0.04479786 0.01530601]
#Converged [0.15210294 0.02410661] [0.04493603 0.01168446]

Using test set # 1

 Distortion t:  [0.01846772 0.03725204 0.06911215] r:  [1.98383737 2.69408367 2.09597257] 

#   0: nll: 0.96/0.84, mi: -0.716/-0.111, acc: 45.0/54.7, eps: 0.13495, R=[1.92, 2.64, 2.04], t=0.10, Q_cos=3.82
#  30: nll: 0.56/0.66, mi:  0.741/ 0.234, acc: 75.0/64.8, eps: 0.07607, R=[1.79, 2.09, 1.59], t=0.20, Q_cos=3.16
#  60: nll: 0.68/0.61, mi:  0.052/ 0.395, acc: 60.0/65.2, eps: 0.00258, R=[1.61, 2.02, 1.54], t=0.20, Q_cos=2.99
Saved checkpoint
#  90: nll: 0.55/0.53, mi:  0.462/ 0.628, acc: 72.5/72.5, eps: 0.01201, R=[1.55, 1.84, 1.63], t=0.21, Q_cos=2.89
Saved checkpoint
# 120: nll: 0.51/0.56, mi:  0.873/ 0.653, acc: 72.5/70.5, eps: 0.00817, R=[1.55, 1.88, 1.79], t=0.20, Q_cos=3.01
Saved checkpoint
# 150: nll: 0.62/0.57, mi:  0.420/ 0.567, acc: 62.5/70.7, eps: 0.02790, R=[1.61, 1.65, 2.26], t=0.23, Q_cos=3.22
# 180: nll: 0.58/0.56, mi:  0.458/ 0.525, acc: 60.0/70.5, eps: 0.00224, R=[1.37, 1.79, 2.18], t=0.23, Q_cos=3.12
# 210: nll: 0.55/0.57, mi:  0.689/ 0.492, acc:

NameError: name 'log_results' is not defined

In [119]:
log = []
np.random.seed(2)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.16516741 0.10232432 0.30963548] r:  [1.49827337 1.33413638 3.10566916] 

#   0: nll: 1.08/0.90, mi: -0.788/-0.393, acc: 45.0/53.0, eps: 0.36651, R=[1.44, 1.28, 3.05], t=0.36, Q_cos=3.59
#  30: nll: 0.61/0.63, mi:  0.368/ 0.249, acc: 62.5/66.0, eps: 0.04018, R=[1.32, 0.66, 2.31], t=0.40, Q_cos=2.73
#  60: nll: 0.67/0.76, mi:  0.271/-0.106, acc: 65.0/60.7, eps: 0.08577, R=[1.23, 0.74, 2.05], t=0.31, Q_cos=2.50
#  90: nll: 0.42/0.59, mi:  1.194/ 0.295, acc: 80.0/70.0, eps: 0.04534, R=[1.04, 0.7, 2.08], t=0.27, Q_cos=2.43
Saved checkpoint
# 120: nll: 0.53/0.52, mi:  0.333/ 0.826, acc: 75.0/72.5, eps: 0.00499, R=[0.82, 0.57, 1.78], t=0.28, Q_cos=2.03
Saved checkpoint
# 150: nll: 0.52/0.54, mi:  0.402/ 0.643, acc: 80.0/73.2, eps: 0.08890, R=[1.12, 0.26, 1.74], t=0.18, Q_cos=2.08
# 180: nll: 0.61/0.49, mi:  0.098/ 1.041, acc: 67.5/75.3, eps: 0.03360, R=[0.93, 0.32, 1.34], t=0.15, Q_cos=1.66
Saved checkpoint
# 210: nll: 0.56/0.45, mi:  0.796/ 1.148, acc: 

In [112]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 7, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [2.77737232 3.77171714 2.9343616 ] 

#   0: nll: 0.91/0.91, mi: -0.692/-0.468, acc: 60.0/54.3, eps: 0.16818, R=[2.72, 3.83, 2.87], t=0.10, Q_cos=5.46
#  30: nll: 0.76/1.00, mi: -0.005/-0.814, acc: 50.0/50.5, eps: 0.02857, R=[2.82, 3.44, 2.22], t=0.15, Q_cos=4.93
#  60: nll: 0.75/0.79, mi: -0.300/-0.206, acc: 60.0/53.2, eps: 0.04955, R=[2.61, 3.59, 2.6], t=0.21, Q_cos=5.10
#  90: nll: 0.55/0.60, mi:  0.529/ 0.373, acc: 75.0/68.7, eps: 0.00331, R=[2.55, 3.57, 2.61], t=0.21, Q_cos=5.06
# 120: nll: 0.76/0.75, mi: -0.227/-0.153, acc: 52.5/58.3, eps: 0.02044, R=[2.48, 3.45, 2.69], t=0.23, Q_cos=4.99
# 150: nll: 0.68/0.65, mi: -0.045/ 0.200, acc: 62.5/60.8, eps: 0.00807, R=[2.45, 3.09, 2.43], t=0.23, Q_cos=4.60
# 180: nll: 0.58/0.61, mi:  0.692/ 0.340, acc: 67.5/65.8, eps: 0.01579, R=[2.23, 3.11, 2.12], t=0.25, Q_cos=4.35
# 210: nll: 0.61/0.56, mi:  0.323/ 0.550, acc: 62.5/70.3, eps: 0.00459, R=[2.32, 3.09, 2.49], t=0.

In [113]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
        
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )

    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 7, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [2.77737232 3.77171714 2.9343616 ] 

#   0: nll: 1.18/0.92, mi: -1.467/-0.376, acc: 55.0/55.0, eps: 0.23677, R=[2.72, 3.72, 2.87], t=0.20, Q_cos=5.38
#  30: nll: 0.87/0.75, mi: -0.192/-0.165, acc: 50.0/57.0, eps: 0.00432, R=[2.48, 3.43, 2.44], t=0.21, Q_cos=4.85
#  60: nll: 0.73/0.69, mi: -0.225/ 0.041, acc: 57.5/60.5, eps: 0.01420, R=[2.43, 3.3, 2.35], t=0.20, Q_cos=4.68
#  90: nll: 0.53/0.69, mi:  0.733/ 0.042, acc: 70.0/58.5, eps: 0.00444, R=[2.31, 3.11, 2.39], t=0.20, Q_cos=4.52
Saved checkpoint
# 120: nll: 0.64/0.55, mi:  0.122/ 0.535, acc: 67.5/72.3, eps: 0.03005, R=[2.27, 3.45, 2.38], t=0.23, Q_cos=4.73
Saved checkpoint
# 150: nll: 0.53/0.67, mi:  0.579/ 0.102, acc: 75.0/61.0, eps: 0.00357, R=[2.24, 3.3, 2.12], t=0.23, Q_cos=4.48
# 180: nll: 0.68/0.66, mi: -0.123/ 0.203, acc: 57.5/57.5, eps: 0.02321, R=[2.4, 3.15, 1.95], t=0.21, Q_cos=4.39
# 210: nll: 0.58/0.64, mi:  0.488/ 0.234, acc: 62.5/64.0, eps: 0.0

In [114]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 8, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [3.17413979 4.31053387 3.35355612] 

#   0: nll: 0.92/0.92, mi: -0.177/-0.310, acc: 52.5/57.2, eps: 0.18514, R=[3.23, 4.25, 3.3], t=0.10, Q_cos=6.21
#  30: nll: 0.98/0.82, mi: -0.649/-0.254, acc: 50.0/53.7, eps: 0.01462, R=[3.22, 4.52, 2.79], t=0.13, Q_cos=6.15
#  60: nll: 0.76/0.85, mi: -0.067/-0.527, acc: 55.0/51.2, eps: 0.04243, R=[2.99, 4.49, 2.65], t=0.19, Q_cos=5.96
#  90: nll: 0.60/0.73, mi:  0.329/-0.056, acc: 65.0/55.3, eps: 0.02183, R=[2.57, 4.91, 2.81], t=0.22, Q_cos=6.16
# 120: nll: 0.61/0.62, mi:  0.387/ 0.312, acc: 60.0/64.2, eps: 0.02344, R=[2.22, 5.14, 2.68], t=0.24, Q_cos=6.16
# 150: nll: 0.56/0.71, mi:  0.513/-0.025, acc: 70.0/60.7, eps: 0.00589, R=[2.05, 5.26, 2.74], t=0.25, Q_cos=6.24
# 180: nll: 0.57/0.60, mi:  0.378/ 0.410, acc: 77.5/69.0, eps: 0.00613, R=[1.95, 5.33, 2.68], t=0.24, Q_cos=6.23
Saved checkpoint
# 210: nll: 0.72/0.67, mi: -0.102/ 0.136, acc: 62.5/60.7, eps: 0.02134, R=[2.02, 

In [115]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
        
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 8, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [3.17413979 4.31053387 3.35355612] 

#   0: nll: 1.21/0.90, mi: -1.228/-0.434, acc: 47.5/51.8, eps: 0.24123, R=[3.23, 4.25, 3.3], t=0.19, Q_cos=6.21
#  30: nll: 1.31/1.00, mi: -1.868/-0.747, acc: 35.0/47.0, eps: 0.01288, R=[2.79, 3.49, 2.85], t=0.19, Q_cos=5.25
#  60: nll: 0.75/0.74, mi: -0.137/-0.141, acc: 55.0/56.0, eps: 0.07943, R=[2.59, 3.33, 2.59], t=0.28, Q_cos=4.91
#  90: nll: 0.59/0.57, mi:  0.312/ 0.484, acc: 70.0/69.3, eps: 0.06217, R=[2.7, 2.85, 2.32], t=0.35, Q_cos=4.53
# 120: nll: 0.50/0.63, mi:  1.037/ 0.250, acc: 85.0/64.3, eps: 0.04177, R=[2.51, 2.67, 2.23], t=0.40, Q_cos=4.26
# 150: nll: 0.51/0.56, mi:  0.792/ 0.557, acc: 82.5/72.3, eps: 0.01735, R=[2.48, 2.7, 2.2], t=0.42, Q_cos=4.24
Saved checkpoint
# 180: nll: 0.59/0.62, mi:  0.333/ 0.337, acc: 75.0/66.5, eps: 0.06431, R=[2.17, 2.49, 2.13], t=0.48, Q_cos=3.90
# 210: nll: 0.50/0.60, mi:  0.603/ 0.416, acc: 82.5/71.0, eps: 0.02624, R=[2.07, 2.2

In [116]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 9, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [3.57090727 4.84935061 3.77275063] 

#   0: nll: 1.11/0.95, mi: -0.743/-0.544, acc: 52.5/51.2, eps: 0.20241, R=[3.62, 4.79, 3.83], t=0.10, Q_cos=7.04
#  30: nll: 0.92/0.85, mi: -0.601/-0.362, acc: 45.0/52.5, eps: 0.01692, R=[3.42, 4.36, 3.37], t=0.15, Q_cos=6.41
#  60: nll: 0.53/0.81, mi:  0.891/-0.397, acc: 67.5/54.0, eps: 0.01328, R=[3.23, 4.34, 3.0], t=0.18, Q_cos=6.12
#  90: nll: 0.70/0.65, mi:  0.135/ 0.193, acc: 57.5/63.8, eps: 0.05383, R=[3.31, 3.79, 2.86], t=0.25, Q_cos=5.74
# 120: nll: 0.71/0.72, mi:  0.006/-0.097, acc: 47.5/53.5, eps: 0.01325, R=[3.42, 3.88, 2.74], t=0.23, Q_cos=5.80
# 150: nll: 0.64/0.67, mi:  0.235/ 0.158, acc: 62.5/62.2, eps: 0.00729, R=[3.34, 3.75, 2.46], t=0.23, Q_cos=5.54
# 180: nll: 0.69/0.63, mi:  0.030/ 0.332, acc: 67.5/64.0, eps: 0.01218, R=[3.02, 3.78, 2.57], t=0.24, Q_cos=5.43
Saved checkpoint
# 210: nll: 0.88/0.71, mi: -0.669/-0.012, acc: 37.5/57.2, eps: 0.04508, R=[3.0, 4

In [127]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
      
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
      
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.000000001, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=False)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [9.23385948e-11 1.86260211e-10 3.45560727e-10] r:  [1.98383737 2.69408367 2.09597257] 

#   0: nll: 1.24/0.89, mi: -1.448/-0.409, acc: 40.0/53.0, eps: 0.09923, R=[2.04, 2.75, 2.16], t=0.00, Q_cos=4.02
#  30: nll: 0.88/0.77, mi: -0.514/-0.268, acc: 50.0/54.0, eps: 0.01046, R=[2.21, 2.26, 1.77], t=0.00, Q_cos=3.60
#  60: nll: 0.72/0.76, mi:  0.143/-0.348, acc: 62.5/56.2, eps: 0.00799, R=[1.89, 2.07, 1.72], t=0.00, Q_cos=3.27
#  90: nll: 0.81/0.67, mi: -0.109/ 0.203, acc: 62.5/63.5, eps: 0.00776, R=[1.69, 1.72, 1.74], t=0.00, Q_cos=2.96
# 120: nll: 0.57/0.62, mi:  0.558/ 0.359, acc: 65.0/66.5, eps: 0.00064, R=[1.58, 1.71, 1.8], t=0.00, Q_cos=2.93
Saved checkpoint
# 150: nll: 0.54/0.65, mi:  0.564/ 0.197, acc: 67.5/59.2, eps: 0.00417, R=[1.39, 1.55, 1.84], t=0.00, Q_cos=2.76
# 180: nll: 0.76/0.59, mi: -0.122/ 0.428, acc: 60.0/69.0, eps: 0.00082, R=[1.67, 1.46, 1.72], t=0.00, Q_cos=2.80
Saved checkpoint
# 210: nll: 0.54/0.62, mi:  0.845/ 0.270, acc: 77.5/

In [118]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 0.000000001, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=False,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [3.96767474e-10 5.38816734e-10 4.19194514e-10] 

#   0: nll: 0.49/0.51, mi:  1.197/ 0.969, acc: 70.0/72.7, eps: 0.19121, R=[0.0, 0.0, 0.0], t=0.19, Q_cos=0.00
#  30: nll: 0.43/0.37, mi:  1.398/ 1.720, acc: 77.5/84.0, eps: 0.14145, R=[0.0, 0.0, 0.0], t=0.05, Q_cos=0.00
Saved checkpoint
#  60: nll: 0.59/0.50, mi:  0.257/ 1.055, acc: 67.5/76.0, eps: 0.01021, R=[0.0, 0.0, 0.0], t=0.06, Q_cos=0.00
#  90: nll: 0.38/0.40, mi:  1.726/ 1.576, acc: 77.5/81.0, eps: 0.01354, R=[0.0, 0.0, 0.0], t=0.07, Q_cos=0.00
# 120: nll: 0.71/0.38, mi:  0.226/ 1.706, acc: 50.0/85.0, eps: 0.06422, R=[0.0, 0.0, 0.0], t=0.01, Q_cos=0.00
# 150: nll: 0.28/0.34, mi:  2.479/ 2.017, acc: 90.0/87.5, eps: 0.05751, R=[0.0, 0.0, 0.0], t=0.07, Q_cos=0.00
Saved checkpoint
# 180: nll: 0.37/0.37, mi:  2.069/ 1.836, acc: 77.5/82.5, eps: 0.01612, R=[0.0, 0.0, 0.0], t=0.05, Q_cos=0.00
# 210: nll: 0.43/0.40, mi:  1.352/ 1.431, acc: 82.5/81.2, eps: 0.02748, 

In [133]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.2, (3,))
    interval_r = np.random.uniform(0, 2, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 1

 Distortion t:  [0.01846772 0.03725204 0.06911215] r:  [0.79353495 1.07763347 0.83838903] 

#   0: nll: 0.99/0.82, mi: -0.919/-0.135, acc: 45.0/56.0, eps: 0.10004, R=[0.74, 1.02, 0.89], t=0.09, Q_cos=1.54
#  30: nll: 0.33/0.42, mi:  2.035/ 1.342, acc: 87.5/81.0, eps: 0.04454, R=[0.34, 0.63, 0.14], t=0.14, Q_cos=0.73
#  60: nll: 0.35/0.43, mi:  1.923/ 1.165, acc: 87.5/78.7, eps: 0.03642, R=[0.38, 0.52, 0.08], t=0.11, Q_cos=0.64
#  90: nll: 0.60/0.43, mi:  0.251/ 1.432, acc: 72.5/82.8, eps: 0.03740, R=[0.35, 0.5, 0.02], t=0.07, Q_cos=0.61
Saved checkpoint
# 120: nll: 0.44/0.42, mi:  1.126/ 1.253, acc: 80.0/81.7, eps: 0.01988, R=[0.4, 0.33, 0.19], t=0.09, Q_cos=0.56
# 150: nll: 0.48/0.44, mi:  0.955/ 1.244, acc: 80.0/81.8, eps: 0.00950, R=[0.15, 0.39, 0.25], t=0.10, Q_cos=0.49
# 180: nll: 0.49/0.49, mi:  1.200/ 1.270, acc: 72.5/79.2, eps: 0.03211, R=[0.29, 0.31, 0.14], t=0.07, Q_cos=0.45
# 210: nll: 0.37/0.46, mi:  2.217/ 1.396, acc: 82.5/78.5, eps: 0.00631, R=[0.08, 0

In [131]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
        
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.6, (3,))
    interval_r = np.random.uniform(0, 2, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)

Using test set # 1

 Distortion t:  [0.05540316 0.11175613 0.20733644] r:  [0.79353495 1.07763347 0.83838903] 

#   0: nll: 0.73/0.76, mi: -0.067/ 0.144, acc: 50.0/60.0, eps: 0.26042, R=[0.74, 1.14, 0.78], t=0.26, Q_cos=1.56
#  30: nll: 0.40/0.53, mi:  1.459/ 0.827, acc: 82.5/75.2, eps: 0.00791, R=[0.55, 0.58, 0.43], t=0.27, Q_cos=0.91
Saved checkpoint
#  60: nll: 0.45/0.39, mi:  1.340/ 1.565, acc: 65.0/84.2, eps: 0.10057, R=[0.56, 0.43, 0.22], t=0.17, Q_cos=0.74
Saved checkpoint
#  90: nll: 0.27/0.60, mi:  2.370/ 0.673, acc: 92.5/71.5, eps: 0.04751, R=[0.33, 0.42, 0.31], t=0.12, Q_cos=0.61
# 120: nll: 0.33/0.39, mi:  1.860/ 1.420, acc: 85.0/83.5, eps: 0.03050, R=[0.52, 0.34, 0.0], t=0.09, Q_cos=0.62
# 150: nll: 0.46/0.40, mi:  0.934/ 1.415, acc: 75.0/81.5, eps: 0.03066, R=[0.41, 0.32, -0.17], t=0.06, Q_cos=0.54
# 180: nll: 0.46/0.50, mi:  1.128/ 0.932, acc: 85.0/75.3, eps: 0.02460, R=[0.42, 0.24, 0.22], t=0.03, Q_cos=0.53
# 210: nll: 0.45/0.47, mi:  1.521/ 1.224, acc: 72.5/78.0, eps: 

In [134]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [1.98383737 2.69408367 2.09597257] 

#   0: nll: 0.81/0.97, mi:  0.328/-0.397, acc: 60.0/52.7, eps: 0.14039, R=[1.92, 2.64, 2.04], t=0.10, Q_cos=3.82
#  30: nll: 0.57/0.66, mi:  0.594/ 0.183, acc: 67.5/61.0, eps: 0.07138, R=[2.01, 2.09, 1.99], t=0.19, Q_cos=3.50
#  60: nll: 0.65/0.54, mi:  0.079/ 0.663, acc: 67.5/74.2, eps: 0.04283, R=[1.68, 1.9, 1.8], t=0.24, Q_cos=3.09
Saved checkpoint
#  90: nll: 0.56/0.63, mi:  0.627/ 0.248, acc: 70.0/67.5, eps: 0.02316, R=[1.4, 1.59, 1.64], t=0.27, Q_cos=2.66
# 120: nll: 0.47/0.56, mi:  0.905/ 0.685, acc: 75.0/71.8, eps: 0.02048, R=[1.28, 1.46, 1.49], t=0.29, Q_cos=2.44
Saved checkpoint
# 150: nll: 0.53/0.52, mi:  0.709/ 0.759, acc: 75.0/72.5, eps: 0.05317, R=[1.36, 1.32, 1.03], t=0.24, Q_cos=2.15
Saved checkpoint
# 180: nll: 0.49/0.54, mi:  1.036/ 0.626, acc: 75.0/70.7, eps: 0.02917, R=[1.07, 1.26, 1.02], t=0.21, Q_cos=1.93
# 210: nll: 0.44/0.46, mi:  1.071/ 1.090, acc: 82

In [135]:
log = []
np.random.seed(2)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.16516741 0.10232432 0.30963548] r:  [1.49827337 1.33413638 3.10566916] 

#   0: nll: 1.08/0.90, mi: -0.788/-0.393, acc: 45.0/53.0, eps: 0.36651, R=[1.44, 1.28, 3.05], t=0.36, Q_cos=3.59
#  30: nll: 0.54/0.68, mi:  0.955/ 0.115, acc: 77.5/63.0, eps: 0.04014, R=[1.33, 1.07, 2.17], t=0.40, Q_cos=2.75
#  60: nll: 0.45/0.52, mi:  0.967/ 0.772, acc: 85.0/76.3, eps: 0.00062, R=[1.16, 0.59, 2.39], t=0.40, Q_cos=2.71
Saved checkpoint
#  90: nll: 0.55/0.51, mi:  0.929/ 0.707, acc: 72.5/75.8, eps: 0.11352, R=[1.14, 0.59, 1.62], t=0.29, Q_cos=2.06
# 120: nll: 0.48/0.49, mi:  1.058/ 0.926, acc: 82.5/75.0, eps: 0.03090, R=[1.09, 0.44, 1.01], t=0.26, Q_cos=1.55
Saved checkpoint
# 150: nll: 0.45/0.65, mi:  1.262/ 0.425, acc: 82.5/65.0, eps: 0.03087, R=[1.08, 0.34, 0.78], t=0.23, Q_cos=1.37
# 180: nll: 0.41/0.42, mi:  1.439/ 1.331, acc: 80.0/80.2, eps: 0.00005, R=[0.83, 0.28, 0.75], t=0.23, Q_cos=1.15
Saved checkpoint
# 210: nll: 0.40/0.50, mi:  1.570/ 0.913, acc:

In [136]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 7, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [2.77737232 3.77171714 2.9343616 ] 

#   0: nll: 0.91/0.91, mi: -0.692/-0.468, acc: 60.0/54.3, eps: 0.16818, R=[2.72, 3.83, 2.87], t=0.10, Q_cos=5.46
#  30: nll: 1.09/0.75, mi: -1.057/-0.131, acc: 50.0/57.2, eps: 0.02083, R=[2.57, 3.32, 1.97], t=0.15, Q_cos=4.61
#  60: nll: 0.60/0.60, mi:  0.582/ 0.378, acc: 72.5/69.0, eps: 0.01789, R=[2.37, 3.63, 1.79], t=0.17, Q_cos=4.66
#  90: nll: 0.59/0.64, mi:  0.292/ 0.279, acc: 67.5/64.3, eps: 0.03128, R=[2.17, 3.43, 1.72], t=0.21, Q_cos=4.38
# 120: nll: 0.54/0.61, mi:  0.641/ 0.341, acc: 72.5/66.0, eps: 0.02304, R=[2.33, 3.41, 1.31], t=0.19, Q_cos=4.31
# 150: nll: 0.51/0.53, mi:  0.598/ 0.729, acc: 77.5/73.5, eps: 0.00023, R=[2.3, 3.59, 1.39], t=0.18, Q_cos=4.46
Saved checkpoint
# 180: nll: 0.65/0.66, mi:  0.234/ 0.151, acc: 62.5/64.7, eps: 0.01127, R=[2.25, 3.57, 1.51], t=0.20, Q_cos=4.46
# 210: nll: 0.52/0.59, mi:  0.696/ 0.450, acc: 80.0/69.5, eps: 0.01736, R=[2.33, 

In [137]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
        
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )

    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 7, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [2.77737232 3.77171714 2.9343616 ] 

#   0: nll: 1.18/0.92, mi: -1.467/-0.376, acc: 55.0/55.0, eps: 0.23677, R=[2.72, 3.72, 2.87], t=0.20, Q_cos=5.38
#  30: nll: 0.93/0.68, mi: -0.499/ 0.088, acc: 55.0/58.3, eps: 0.12462, R=[2.33, 3.73, 2.48], t=0.34, Q_cos=5.01
#  60: nll: 0.75/0.71, mi: -0.108/ 0.018, acc: 57.5/58.0, eps: 0.04182, R=[2.17, 3.74, 2.46], t=0.38, Q_cos=4.94
#  90: nll: 0.54/0.59, mi:  0.601/ 0.434, acc: 82.5/67.5, eps: 0.03223, R=[2.22, 3.47, 2.24], t=0.42, Q_cos=4.66
Saved checkpoint
# 120: nll: 0.69/0.55, mi: -0.106/ 0.606, acc: 52.5/73.0, eps: 0.01256, R=[2.14, 3.21, 2.28], t=0.43, Q_cos=4.45
Saved checkpoint
# 150: nll: 0.60/0.52, mi:  0.444/ 0.765, acc: 67.5/75.5, eps: 0.03951, R=[2.13, 2.86, 2.24], t=0.48, Q_cos=4.19
Saved checkpoint
# 180: nll: 0.59/0.66, mi:  0.519/ 0.131, acc: 70.0/63.0, eps: 0.04307, R=[2.12, 2.6, 2.2], t=0.52, Q_cos=3.99
# 210: nll: 0.43/0.50, mi:  1.216/ 0.886, acc: 8

In [138]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 8, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [3.17413979 4.31053387 3.35355612] 

#   0: nll: 0.92/0.92, mi: -0.177/-0.309, acc: 52.5/57.2, eps: 0.18514, R=[3.23, 4.25, 3.3], t=0.10, Q_cos=6.21
#  30: nll: 0.72/0.83, mi:  0.164/-0.302, acc: 60.0/55.7, eps: 0.02923, R=[2.99, 3.42, 3.55], t=0.07, Q_cos=5.71
#  60: nll: 0.57/0.60, mi:  0.540/ 0.410, acc: 72.5/67.5, eps: 0.00666, R=[2.79, 3.53, 3.81], t=0.04, Q_cos=5.84
#  90: nll: 0.71/0.71, mi: -0.008/-0.018, acc: 45.0/56.8, eps: 0.00900, R=[2.74, 3.49, 3.96], t=0.06, Q_cos=5.89
# 120: nll: 0.58/0.66, mi:  0.500/ 0.071, acc: 70.0/62.5, eps: 0.02620, R=[2.5, 3.27, 3.85], t=0.12, Q_cos=5.59
# 150: nll: 0.62/0.57, mi:  0.401/ 0.596, acc: 60.0/72.7, eps: 0.02097, R=[2.75, 3.33, 3.74], t=0.08, Q_cos=5.66
Saved checkpoint
# 180: nll: 0.55/0.64, mi:  0.767/ 0.221, acc: 77.5/64.0, eps: 0.00551, R=[2.68, 3.45, 3.79], t=0.07, Q_cos=5.73
# 210: nll: 0.57/0.61, mi:  0.787/ 0.350, acc: 65.0/65.0, eps: 0.01665, R=[2.84, 3

In [139]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
        
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 8, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [3.17413979 4.31053387 3.35355612] 

#   0: nll: 1.21/0.90, mi: -1.228/-0.434, acc: 47.5/51.8, eps: 0.24123, R=[3.23, 4.25, 3.3], t=0.19, Q_cos=6.21
#  30: nll: 0.75/0.94, mi: -0.158/-0.634, acc: 40.0/50.5, eps: 0.03688, R=[3.18, 4.72, 3.41], t=0.23, Q_cos=6.57
#  60: nll: 0.56/0.64, mi:  0.594/ 0.291, acc: 67.5/66.0, eps: 0.01527, R=[3.38, 4.87, 3.2], t=0.24, Q_cos=6.67
#  90: nll: 0.78/0.62, mi: -0.399/ 0.316, acc: 45.0/63.8, eps: 0.03950, R=[3.49, 4.61, 3.15], t=0.20, Q_cos=6.51
Saved checkpoint
# 120: nll: 0.61/0.65, mi:  0.458/ 0.172, acc: 65.0/63.5, eps: 0.02293, R=[3.39, 4.63, 3.0], t=0.23, Q_cos=6.41
# 150: nll: 0.76/0.68, mi: -0.049/ 0.064, acc: 60.0/57.7, eps: 0.01462, R=[3.25, 4.62, 3.03], t=0.25, Q_cos=6.34
# 180: nll: 0.56/0.53, mi:  0.578/ 0.763, acc: 72.5/73.0, eps: 0.01195, R=[3.33, 4.52, 3.14], t=0.26, Q_cos=6.36
Saved checkpoint
# 210: nll: 0.62/0.61, mi:  0.289/ 0.316, acc: 62.5/67.8, eps: 0.0

In [140]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.25, (3,))
    interval_r = np.random.uniform(0, 9, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.02308465 0.04656505 0.08639018] r:  [3.57090727 4.84935061 3.77275063] 

#   0: nll: 1.11/0.95, mi: -0.743/-0.546, acc: 52.5/51.2, eps: 0.20241, R=[3.62, 4.79, 3.83], t=0.10, Q_cos=7.04
#  30: nll: 1.14/0.70, mi: -1.289/ 0.069, acc: 22.5/58.5, eps: 0.04282, R=[3.77, 5.0, 3.87], t=0.17, Q_cos=7.27
#  60: nll: 0.86/0.73, mi: -0.439/-0.080, acc: 42.5/53.0, eps: 0.06443, R=[3.34, 5.34, 3.88], t=0.25, Q_cos=7.31
#  90: nll: 0.47/0.59, mi:  1.093/ 0.504, acc: 82.5/69.0, eps: 0.01673, R=[3.49, 5.09, 3.79], t=0.23, Q_cos=7.16
Saved checkpoint
# 120: nll: 0.68/0.62, mi:  0.117/ 0.305, acc: 65.0/65.7, eps: 0.01866, R=[3.61, 4.85, 3.73], t=0.26, Q_cos=7.02
# 150: nll: 0.70/0.68, mi: -0.034/ 0.033, acc: 55.0/56.2, eps: 0.01718, R=[3.56, 4.73, 3.67], t=0.28, Q_cos=6.88
# 180: nll: 0.58/0.72, mi:  0.572/-0.056, acc: 72.5/55.2, eps: 0.05073, R=[3.44, 4.79, 3.5], t=0.34, Q_cos=6.78
# 210: nll: 0.74/0.61, mi: -0.166/ 0.330, acc: 57.5/66.2, eps: 0.01486, R=[3.57, 4

In [141]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
      
    print("Using test set #", i)
    
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
      
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.000000001, (3,))
    interval_r = np.random.uniform(0, 5, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=True,
                   grad_T=False)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [9.23385948e-11 1.86260211e-10 3.45560727e-10] r:  [1.98383737 2.69408367 2.09597257] 

#   0: nll: 1.24/0.89, mi: -1.448/-0.409, acc: 40.0/53.0, eps: 0.09923, R=[2.04, 2.75, 2.16], t=0.00, Q_cos=4.02
#  30: nll: 0.66/0.67, mi:  0.302/ 0.143, acc: 70.0/58.7, eps: 0.01353, R=[1.55, 2.68, 1.61], t=0.00, Q_cos=3.47
#  60: nll: 0.55/0.66, mi:  0.480/ 0.155, acc: 70.0/61.5, eps: 0.00648, R=[1.57, 2.37, 1.52], t=0.00, Q_cos=3.21
Saved checkpoint
#  90: nll: 0.61/0.65, mi:  0.268/ 0.129, acc: 65.0/62.7, eps: 0.00700, R=[1.33, 2.22, 1.4], t=0.00, Q_cos=2.93
# 120: nll: 0.52/0.53, mi:  0.636/ 0.741, acc: 77.5/72.0, eps: 0.01044, R=[1.13, 1.72, 1.44], t=0.00, Q_cos=2.50
Saved checkpoint
# 150: nll: 0.36/0.47, mi:  1.762/ 1.030, acc: 85.0/80.2, eps: 0.01646, R=[0.81, 0.93, 1.37], t=0.00, Q_cos=1.84
Saved checkpoint
# 180: nll: 0.50/0.50, mi:  0.648/ 0.956, acc: 77.5/74.5, eps: 0.01100, R=[0.68, 0.48, 1.12], t=0.00, Q_cos=1.39
# 210: nll: 0.40/0.47, mi:  1.554/ 

In [142]:
log = []
np.random.seed(1)

for i in np.random.uniform(0 ,len(datas_test), 5).astype(int):
    
    print("Using test set #", i)
    datas_test_ = datas_test[i]
    kitti1 = datas_test_[0]
    
    
    ac = AutoCalibration(kitti1.calib.T_cam2_velo, kitti1.calib.P_rect_20, 
                         max_z=30, pc_batch=5000, mi_batch=20, mi_batches=1,
                         patch_size=96, hidden_size=32,  
                         true_kittis=datas, max_z_true_kittis=30
                         )
    
    ac.to("cuda")
    ac.load_state_dict(torch.load("checkpoints/mi_model_p96_small.pth.tar"))
    ac.reset_calibration()

    interval_t = np.random.uniform(0, 0.5, (3,))
    interval_r = np.random.uniform(0, 0.000000001, (3,))
    print("\n", "Distortion", "t: ", interval_t, "r: ",  interval_r, "\n")
    ac.distort_calibration(interval_t, interval_r)
    
    for iters, lr in [(4000, 1e-3), (1000, 1e-4), (1000, 1e-5), (1000, 1e-6)]:
    
        ac.update_se_and_mine(lr_mi=lr, lr_R=lr, lr_T=10*lr)
        ac.best_mi = 0.
        r = ac.fit(datas_test_, iters=iters, log_interval=30, viz="viz", 
                   log_avg_window=1,
                   n_test_batches=10, 
                   valid_ratio=0.1, 
                   grad_SE=True, 
                   grad_R=False,
                   grad_T=True)
        

    log.append((r, interval_t, interval_r))
    
log_results(log)


Using test set # 1

 Distortion t:  [0.0461693  0.09313011 0.17278036] r:  [3.96767474e-10 5.38816734e-10 4.19194514e-10] 

#   0: nll: 0.49/0.51, mi:  1.197/ 0.969, acc: 70.0/73.0, eps: 0.19121, R=[0.0, 0.0, 0.0], t=0.19, Q_cos=0.00
#  30: nll: 0.37/0.44, mi:  1.503/ 1.379, acc: 92.5/79.7, eps: 0.11961, R=[0.0, 0.0, 0.0], t=0.07, Q_cos=0.00
Saved checkpoint
#  60: nll: 0.83/0.49, mi: -0.323/ 1.033, acc: 57.5/79.0, eps: 0.02606, R=[0.0, 0.0, 0.0], t=0.05, Q_cos=0.00
#  90: nll: 0.32/0.36, mi:  1.939/ 1.770, acc: 85.0/87.0, eps: 0.01230, R=[0.0, 0.0, 0.0], t=0.06, Q_cos=0.00
Saved checkpoint
# 120: nll: 0.42/0.41, mi:  1.275/ 1.522, acc: 77.5/80.7, eps: 0.01428, R=[0.0, 0.0, 0.0], t=0.04, Q_cos=0.00
# 150: nll: 0.59/0.44, mi:  0.668/ 1.198, acc: 75.0/80.2, eps: 0.01196, R=[0.0, 0.0, 0.0], t=0.03, Q_cos=0.00
# 180: nll: 0.43/0.39, mi:  1.866/ 1.760, acc: 82.5/81.7, eps: 0.01030, R=[0.0, 0.0, 0.0], t=0.02, Q_cos=0.00
# 210: nll: 0.31/0.40, mi:  2.427/ 1.469, acc: 85.0/81.7, eps: 0.02925, 